In [0]:
from google.colab import drive
drive.mount('/content/drive')

In [0]:
#!pip install -U -q PyDrive
#from pydrive.auth import GoogleAuth
#from pydrive.drive import GoogleDrive
#from google.colab import auth
#from oauth2client.client import GoogleCredentials
## Authenticate and create the PyDrive client.
## This only needs to be done once per notebook.
#auth.authenticate_user()
#gauth = GoogleAuth()
#gauth.credentials = GoogleCredentials.get_application_default()
#drive = GoogleDrive(gauth)
##https://drive.google.com/open?id=0B7EVK8r0v71pZjFTYXZWM3FlRnM
#file_id = '0B7EVK8r0v71pZjFTYXZWM3FlRnM' # URL id. 
#downloaded = drive.CreateFile({'id': file_id})
#downloaded.GetContentFile('img_align_celeba.zip')

#!mkdir data
#!mv img_align_celeba.zip data/

In [0]:
!mkdir data
#!ls "drive/My Drive/ECE697/"
!cp "drive/My Drive/ECE697/img_align_celeba.zip" "data/img_align_celeba.zip"

In [0]:
!apt-get install imagemagick

Reading package lists... Done
Building dependency tree       
Reading state information... Done
The following additional packages will be installed:
  fonts-droid-fallback fonts-noto-mono ghostscript gsfonts
  imagemagick-6-common imagemagick-6.q16 libcupsfilters1 libcupsimage2
  libdjvulibre-text libdjvulibre21 libgs9 libgs9-common libijs-0.35
  libjbig2dec0 liblqr-1-0 libmagickcore-6.q16-3 libmagickcore-6.q16-3-extra
  libmagickwand-6.q16-3 libnetpbm10 libwmf0.2-7 netpbm poppler-data
Suggested packages:
  fonts-noto ghostscript-x imagemagick-doc autotrace cups-bsd | lpr | lprng
  enscript gimp gnuplot grads hp2xx html2ps libwmf-bin mplayer povray radiance
  sane-utils texlive-base-bin transfig ufraw-batch inkscape libjxr-tools
  libwmf0.2-7-gtk poppler-utils fonts-japanese-mincho | fonts-ipafont-mincho
  fonts-japanese-gothic | fonts-ipafont-gothic fonts-arphic-ukai
  fonts-arphic-uming fonts-nanum
The following NEW packages will be installed:
  fonts-droid-fallback fonts-noto-mono g

In [0]:
# Process dsprites data
#!bash scripts/prepare_data.sh dsprites

In [0]:
!bash scripts/prepare_data.sh CelebA

Streaming output truncated to the last 5000 lines.
 extracting: img_align_celeba/197601.jpg  
 extracting: img_align_celeba/197602.jpg  
 extracting: img_align_celeba/197603.jpg  
 extracting: img_align_celeba/197604.jpg  
 extracting: img_align_celeba/197605.jpg  
 extracting: img_align_celeba/197606.jpg  
 extracting: img_align_celeba/197607.jpg  
 extracting: img_align_celeba/197608.jpg  
 extracting: img_align_celeba/197609.jpg  
 extracting: img_align_celeba/197610.jpg  
 extracting: img_align_celeba/197611.jpg  
 extracting: img_align_celeba/197612.jpg  
 extracting: img_align_celeba/197613.jpg  
 extracting: img_align_celeba/197614.jpg  
 extracting: img_align_celeba/197615.jpg  
 extracting: img_align_celeba/197616.jpg  
 extracting: img_align_celeba/197617.jpg  
 extracting: img_align_celeba/197618.jpg  
 extracting: img_align_celeba/197619.jpg  
 extracting: img_align_celeba/197620.jpg  
 extracting: img_align_celeba/197621.jpg  
 extracting: img_align_celeba/197622.jpg  
 ex

In [0]:
#!bash scripts/prepare_data.sh 3DChairs
#!bash scripts/prepare_data.sh 3DChairs

In [0]:
"""main.py"""

import numpy as np
import torch
import os
import subprocess

from solver import Solver

torch.backends.cudnn.enabled = True
torch.backends.cudnn.benchmark = True

parameters1 = {'start_fresh'       : False,
              'train'             : True,
              'use_cuda'          : True,
              'seed'              : 1,
              'max_iter'          : 1.5e6,
              'z_dim'             : 32,
              'beta'              : 250,
              'model'             : 'H',
              'objective'         : 'H',
              'lr'                : 1e-4,
              'beta1'             : 0.9,
              'beta2'             : 0.999,
              'ckpt_dir'          : 'checkpoints',
              'tensorboard_dir'   : 'tnsrbrd_runs',
              'project_name'      : 'celeba_H_beta250_z32',
              'ckpt_name'         : 'last',
              'save_output'       : True,
              'output_dir'        : 'outputs',
              'gather_step'       : 1000,
              'display_step'      : 10000,
              'save_step'         : 10000,
              'dset_dir'          : 'data',
              'dataset'           : 'CelebA',
              'batch_size'        : 64,
              'num_workers'       : 2,
              'image_size'        : 64,
              'viz_on'            : True
              }

parameters2 = {'start_fresh'       : True,
              'train'             : True,
              'use_cuda'          : True,
              'seed'              : 1,
              'max_iter'          : 1.5e6,
              'z_dim'             : 16,
              'beta'              : 10,
              'model'             : 'H',
              'objective'         : 'H',
              'lr'                : 1e-4,
              'beta1'             : 0.9,
              'beta2'             : 0.999,
              'ckpt_dir'          : 'checkpoints',
              'tensorboard_dir'   : 'tnsrbrd_runs',
              'project_name'      : 'celeba_H_beta10_z10',
              'ckpt_name'         : 'last',
              'save_output'       : True,
              'output_dir'        : 'outputs',
              'gather_step'       : 100,
              'display_step'      : 1000,
              'save_step'         : 1000,
              'dset_dir'          : 'data',
              'dataset'           : 'CelebA',
              'batch_size'        : 64,
              'num_workers'       : 2,
              'image_size'        : 64,
              'viz_on'            : True
              }

parameters1_drive = {'start_fresh'       : False,
              'train'             : True,
              'use_cuda'          : True,
              'seed'              : 1,
              'max_iter'          : 1.5e6,
              'z_dim'             : 32,
              'beta'              : 15,
              'model'             : 'H',
              'objective'         : 'H',
              'lr'                : 1e-4,
              'beta1'             : 0.9,
              'beta2'             : 0.999,
              'ckpt_dir'          : 'drive/My Drive/ECE697/checkpoints',
              'tensorboard_dir'   : 'drive/My Drive/ECE697/tnsrbrd_runs',
              'project_name'      : 'celeba_H_beta15_z32',
              'ckpt_name'         : 'last',
              'save_output'       : True,
              'output_dir'        : 'drive/My Drive/ECE697/outputs',
              'gather_step'       : 1000,
              'display_step'      : 10000,
              'save_step'         : 10000,
              'dset_dir'          : 'data',
              'dataset'           : 'CelebA',
              'batch_size'        : 64,
              'num_workers'       : 2,
              'image_size'        : 64,
              'viz_on'            : True
              }

parameters = parameters1_drive

if parameters['start_fresh']:
  str1 = 'rm -rf '+os.path.join(parameters['ckpt_dir'], parameters['project_name']) 
  subprocess.call(str1, shell=True)
  str1 = 'rm -rf '+os.path.join(parameters['output_dir'], parameters['project_name']) 
  subprocess.call(str1, shell=True)
  str1 = 'rm -rf '+os.path.join(parameters['tensorboard_dir'], parameters['project_name']) 
  subprocess.call(str1, shell=True)

torch.manual_seed(parameters['seed'])
torch.cuda.manual_seed(parameters['seed'])
np.random.seed(parameters['seed'])

# Load the TensorBoard notebook extension
#!rm -rf {os.path.join(parameters['tensorboard_dir'], parameters['project_name'])} 
#!fuser 6006/tcp -k
%load_ext tensorboard
%tensorboard --logdir {'"'+os.path.join(parameters['tensorboard_dir'], parameters['project_name'])+'"'}

net = net = Solver(parameters)

if parameters['train']:
  net.train()
else:
  net.traverse()

<IPython.core.display.Javascript object>

=> loaded checkpoint 'drive/My Drive/ECE697/checkpoints/celeba_H_beta15_z32/last (iter 1490000)'


100%|██████████| 1500000/1500000.0 [12:09<00:00, 2055.24it/s]


[Training Finished]
